<p align="center"><img width="50%" src="https://aimodelsharecontent.s3.amazonaws.com/aimodshare_banner.jpg" /></p>


---


<p align="center"><h1 align="center">Internet Ad Model Submission Guide - Deep Learning

##### <p align="center">*Data Source: Lichman, M. (2013). [UCI Machine Learning Repository](http://archive.ics.uci.edu/ml) . Irvine, CA: University of California, School of Information and Computer Science.*

---
Let's share our models to a centralized leaderboard, so that we can collaborate and learn from the model experimentation process...

**Instructions:**
1.   Get data in and set up X_train / X_test / y_train
2.   Preprocess data  with Sklearn Column Transformer/ Write and Save Preprocessor function
3. Fit model on preprocessed data and save preprocessor function and model 
4. Generate predictions from X_test data and submit model to competition
5. Repeat submission process to improve place on leaderboard

# Objective: Predict whether an image is an advertisement (ad.) or not (nonad.)

---

**Data**: This dataset represents a set of possible advertisements on Internet pages. The features encode the geometry of the image (if available) as well as phrases occuring in the URL, the image's URL and alt text, the anchor text, and words occuring near the anchor text. 

**Features (1558 features)**
* **height** height of image
* **width** width of image
* **aratio** aspect ratio of image
* **URL Terms** 457 features of page urls 
* **orig URL Terms** 495 features from original image urls
* **anc URL Terms** 472 features from anchor urls
* **alt Terms** 111 features from image alt text
* **caption Terms** 19 features from image captions

**Target**
*   Binary variable (ad./nonad)

## 1. Get data in and set up X_train, X_test, y_train objects

In [2]:
#install aimodelshare library
! pip install aimodelshare --upgrade

In [3]:
# Get competition data
from aimodelshare import download_data
download_data('public.ecr.aws/y2e2a1d6/internet_ads_competition_data-repository:latest')


Data downloaded successfully.


In [4]:
# Load data into X_train, y_train, and X_test
import pandas as pd
X_train = pd.read_csv("internet_ads_competition_data/X_train.csv")
y_train = pd.read_csv("internet_ads_competition_data/y_train.csv", squeeze=True)
y_train = pd.get_dummies(y_train)

X_test=pd.read_csv("internet_ads_competition_data/X_test.csv")

X_train.head()

height  width  aratio  local  url*images+buttons  url*likesbooks.com  \
0    60.0  468.0  7.8000    1.0                   0                   0   
1   120.0  120.0  1.0000    1.0                   0                   0   
2    90.0  128.0  1.4222    0.0                   0                   0   
3    24.0  120.0  5.0000    0.0                   0                   0   
4    77.0  108.0  1.4025    1.0                   0                   0   

   url*www.slake.com  url*hydrogeologist  url*oso  url*media  ...  caption*of  \
0                  0                   0        0          0  ...           0   
1                  0                   0        0          0  ...           0   
2                  0                   0        0          0  ...           0   
3                  0                   0        0          0  ...           0   
4                  0                   0        0          0  ...           0   

   caption*home  caption*my  caption*your  caption*in  caption*bytes  \
0             0           0             0           0              0   
1             0           0             0           0              0   
2             0           0             0           0              0   
3             0           0             0           0              0   
4             0           0             0           0              0   

   caption*here  caption*click  caption*for  caption*you  
0             0              0            0            0  
1             0              0            0            0  
2             0              0            0            0  
3             0              0            0            0  
4             0              0            0            0  

[5 rows x 1558 columns]

In [5]:
print(X_train.shape)
print(X_test.shape)
print(y_train.shape)

(2623, 1558)
(656, 1558)
(2623, 2)


##2.   Preprocess data using Sklearn Column Transformer / Write and Save Preprocessor function


In [6]:
# In this case we use Sklearn's Column transformer in our preprocessor function

from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler, OneHotEncoder

#Preprocess data using sklearn's Column Transformer approach

# We create the preprocessing pipelines for both numeric and categorical data.
numeric_features = ['height', 'width', 'aratio']
numeric_transformer = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='median')), #'imputer' names the step
    ('scaler', StandardScaler())])

binary_features = X_train.columns.tolist()
binary_features = [colname for colname in binary_features if colname not in numeric_features]

# Replacing missing values with Modal value 
categorical_transformer = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='most_frequent'))])

# Final preprocessor object set up with ColumnTransformer...

preprocess = ColumnTransformer(
    transformers=[
        ('num', numeric_transformer, numeric_features),
        ('cat', categorical_transformer, binary_features)])

# fit preprocessor to your data
preprocess = preprocess.fit(X_train)

In [7]:
# Write function to transform data with preprocessor

def preprocessor(data):
    preprocessed_data=preprocess.transform(data)
    return preprocessed_data

In [8]:
# check shape of X data 
preprocessor(X_train).shape

(2623, 1558)

##3. Fit model on preprocessed data and save preprocessor function and model 


### Building 6 keras Models and choosing the best one 

In [9]:
###using categorical_crossentropy, sgd, reLU and softmax
from keras.models import Sequential
from keras.layers import Dense, Activation, Dropout
import keras

feature_count=preprocessor(X_train).shape[1] #count features in input data

model = Sequential()
model.add(Dense(64, input_dim=feature_count, activation='relu'))
model.add(Dense(64, activation='relu'))
model.add(Dense(64, activation='relu'))

model.add(Dense(2, activation='softmax')) 
                                            
# Compile model
model.compile(loss='categorical_crossentropy', optimizer='sgd', metrics=['accuracy'])

# Fitting the NN to the Training set
model.fit(preprocessor(X_train), y_train, 
               batch_size = 20, 
               epochs = 10, validation_split=0.25) 

Epoch 1/10
99/99 [==============================] - 5s 28ms/step - loss: 0.5552 - accuracy: 0.8414 - val_loss: 0.4368 - val_accuracy: 0.8872
Epoch 2/10
99/99 [==============================] - 1s 12ms/step - loss: 0.4083 - accuracy: 0.8622 - val_loss: 0.3467 - val_accuracy: 0.8872
Epoch 3/10
99/99 [==============================] - 1s 12ms/step - loss: 0.3512 - accuracy: 0.8622 - val_loss: 0.2975 - val_accuracy: 0.8872
Epoch 4/10
99/99 [==============================] - 2s 15ms/step - loss: 0.3073 - accuracy: 0.8627 - val_loss: 0.2542 - val_accuracy: 0.8902
Epoch 5/10
99/99 [==============================] - 2s 15ms/step - loss: 0.2640 - accuracy: 0.8882 - val_loss: 0.2139 - val_accuracy: 0.9177
Epoch 6/10
99/99 [==============================] - 2s 16ms/step - loss: 0.2254 - accuracy: 0.9222 - val_loss: 0.1801 - val_accuracy: 0.9543
Epoch 7/10
99/99 [==============================] - 1s 12ms/step - loss: 0.1951 - accuracy: 0.9400 - val_loss: 0.1537 - val_accuracy: 0.9497
Epoch 8/10
99

In [10]:
###used this time binary_crossentropy, adam ,and sigmoid for my code

from keras.models import Sequential
from keras.layers import Dense, Activation, Dropout
import keras

feature_count=preprocessor(X_train).shape[1] #count features in input data

model = Sequential()
model.add(Dense(128, input_dim=feature_count, activation='relu'))
model.add(Dense(256, activation='relu'))
model.add(Dense(256, activation='relu'))

model.add(Dense(2, activation='sigmoid')) 
                                            
# Compile model
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

# Fitting the NN to the Training set
model.fit(preprocessor(X_train), y_train, 
               batch_size = 20, 
               epochs = 7, validation_split=0.25) 

Epoch 1/7
99/99 [==============================] - 1s 8ms/step - loss: 0.2260 - accuracy: 0.9222 - val_loss: 0.0750 - val_accuracy: 0.9817
Epoch 2/7
99/99 [==============================] - 1s 7ms/step - loss: 0.0806 - accuracy: 0.9786 - val_loss: 0.0757 - val_accuracy: 0.9756
Epoch 3/7
99/99 [==============================] - 1s 8ms/step - loss: 0.0473 - accuracy: 0.9832 - val_loss: 0.1125 - val_accuracy: 0.9741
Epoch 4/7
99/99 [==============================] - 1s 7ms/step - loss: 0.0315 - accuracy: 0.9893 - val_loss: 0.0863 - val_accuracy: 0.9832
Epoch 5/7
99/99 [==============================] - 1s 7ms/step - loss: 0.0195 - accuracy: 0.9949 - val_loss: 0.1004 - val_accuracy: 0.9771
Epoch 6/7
99/99 [==============================] - 1s 8ms/step - loss: 0.0216 - accuracy: 0.9949 - val_loss: 0.1065 - val_accuracy: 0.9802
Epoch 7/7
99/99 [==============================] - 1s 7ms/step - loss: 0.0179 - accuracy: 0.9954 - val_loss: 0.1124 - val_accuracy: 0.9771


In [11]:
###used this time categorical_crossentropy, RMSprop ,and sigmoid for my code

from keras.models import Sequential
from keras.layers import Dense, Activation, Dropout
import keras

feature_count=preprocessor(X_train).shape[1] #count features in input data

model = Sequential()
model.add(Dense(128, input_dim=feature_count, activation='relu'))
model.add(Dense(256, activation='relu'))
model.add(Dense(512, activation='relu'))

model.add(Dense(2, activation='sigmoid')) 
                                            
# Compile model
model.compile(loss='categorical_crossentropy', optimizer='RMSprop', metrics=['accuracy'])

# Fitting the NN to the Training set
model.fit(preprocessor(X_train), y_train, 
               batch_size = 20, 
               epochs = 7, validation_split=0.25) 

Epoch 1/7
99/99 [==============================] - 2s 12ms/step - loss: 0.1774 - accuracy: 0.9441 - val_loss: 0.0785 - val_accuracy: 0.9756
Epoch 2/7
99/99 [==============================] - 1s 10ms/step - loss: 0.0827 - accuracy: 0.9751 - val_loss: 0.0803 - val_accuracy: 0.9817
Epoch 3/7
99/99 [==============================] - 1s 10ms/step - loss: 0.0680 - accuracy: 0.9827 - val_loss: 0.0894 - val_accuracy: 0.9817
Epoch 4/7
99/99 [==============================] - 1s 9ms/step - loss: 0.0535 - accuracy: 0.9837 - val_loss: 0.0967 - val_accuracy: 0.9802
Epoch 5/7
99/99 [==============================] - 1s 10ms/step - loss: 0.0364 - accuracy: 0.9888 - val_loss: 0.1366 - val_accuracy: 0.9787
Epoch 6/7
99/99 [==============================] - 1s 8ms/step - loss: 0.0344 - accuracy: 0.9919 - val_loss: 0.1112 - val_accuracy: 0.9802
Epoch 7/7
99/99 [==============================] - 1s 9ms/step - loss: 0.0302 - accuracy: 0.9903 - val_loss: 0.1363 - val_accuracy: 0.9787


In [12]:
###used this time KLDivergence, Adadelta ,and softplus for my code

from keras.models import Sequential
from keras.layers import Dense, Activation, Dropout
import keras

feature_count=preprocessor(X_train).shape[1] #count features in input data

model = Sequential()
model.add(Dense(64, input_dim=feature_count, activation='relu'))
model.add(Dense(128, activation='relu'))
model.add(Dense(128, activation='relu'))

model.add(Dense(2, activation='softplus')) 
                                            
# Compile model
model.compile(loss='KLDivergence', optimizer='Adadelta', metrics=['accuracy'])

# Fitting the NN to the Training set
model.fit(preprocessor(X_train), y_train, 
               batch_size = 20, 
               epochs = 7, validation_split=0.25) 

Epoch 1/7
99/99 [==============================] - 1s 7ms/step - loss: 0.3604 - accuracy: 0.7229 - val_loss: 0.3592 - val_accuracy: 0.7088
Epoch 2/7
99/99 [==============================] - 1s 5ms/step - loss: 0.3569 - accuracy: 0.7422 - val_loss: 0.3556 - val_accuracy: 0.7287
Epoch 3/7
99/99 [==============================] - 0s 5ms/step - loss: 0.3533 - accuracy: 0.7565 - val_loss: 0.3520 - val_accuracy: 0.7576
Epoch 4/7
99/99 [==============================] - 0s 5ms/step - loss: 0.3496 - accuracy: 0.7717 - val_loss: 0.3482 - val_accuracy: 0.7698
Epoch 5/7
99/99 [==============================] - 1s 6ms/step - loss: 0.3458 - accuracy: 0.7865 - val_loss: 0.3443 - val_accuracy: 0.7881
Epoch 6/7
99/99 [==============================] - 0s 5ms/step - loss: 0.3418 - accuracy: 0.8109 - val_loss: 0.3402 - val_accuracy: 0.8140
Epoch 7/7
99/99 [==============================] - 0s 5ms/step - loss: 0.3377 - accuracy: 0.8287 - val_loss: 0.3361 - val_accuracy: 0.8247


In [13]:
###used this time KLDivergence, Adagrad ,and softmax for my code

from keras.models import Sequential
from keras.layers import Dense, Activation, Dropout
import keras

feature_count=preprocessor(X_train).shape[1] #count features in input data

model = Sequential()
model.add(Dense(128, input_dim=feature_count, activation='relu'))
model.add(Dense(128, activation='relu'))
model.add(Dense(128, activation='relu'))

model.add(Dense(2, activation='softmax')) 
                                            
# Compile model
model.compile(loss='KLDivergence', optimizer='Adagrad', metrics=['accuracy'])

# Fitting the NN to the Training set
model.fit(preprocessor(X_train), y_train, 
               batch_size = 20, 
               epochs = 7, validation_split=0.25) 

Epoch 1/7
99/99 [==============================] - 1s 7ms/step - loss: 0.6161 - accuracy: 0.8622 - val_loss: 0.5709 - val_accuracy: 0.8872
Epoch 2/7
99/99 [==============================] - 1s 5ms/step - loss: 0.5526 - accuracy: 0.8622 - val_loss: 0.5094 - val_accuracy: 0.8872
Epoch 3/7
99/99 [==============================] - 1s 5ms/step - loss: 0.4999 - accuracy: 0.8622 - val_loss: 0.4570 - val_accuracy: 0.8872
Epoch 4/7
99/99 [==============================] - 1s 5ms/step - loss: 0.4557 - accuracy: 0.8622 - val_loss: 0.4137 - val_accuracy: 0.8872
Epoch 5/7
99/99 [==============================] - 0s 5ms/step - loss: 0.4197 - accuracy: 0.8622 - val_loss: 0.3783 - val_accuracy: 0.8872
Epoch 6/7
99/99 [==============================] - 1s 5ms/step - loss: 0.3904 - accuracy: 0.8622 - val_loss: 0.3497 - val_accuracy: 0.8872
Epoch 7/7
99/99 [==============================] - 1s 5ms/step - loss: 0.3666 - accuracy: 0.8622 - val_loss: 0.3270 - val_accuracy: 0.8872


In [14]:
###used this time categorical_crossentropy, Adamax ,and softplus for my code

from keras.models import Sequential
from keras.layers import Dense, Activation, Dropout
import keras

feature_count=preprocessor(X_train).shape[1] #count features in input data

model = Sequential()
model.add(Dense(128, input_dim=feature_count, activation='relu'))
model.add(Dense(128, activation='relu'))
model.add(Dense(128, activation='relu'))

model.add(Dense(2, activation='softplus')) 
                                            
# Compile model
model.compile(loss='categorical_crossentropy', optimizer='Adamax', metrics=['accuracy'])

# Fitting the NN to the Training set
model.fit(preprocessor(X_train), y_train, 
               batch_size = 20, 
               epochs = 7, validation_split=0.25) 

Epoch 1/7
99/99 [==============================] - 1s 7ms/step - loss: 0.3173 - accuracy: 0.8846 - val_loss: 0.1289 - val_accuracy: 0.9649
Epoch 2/7
99/99 [==============================] - 1s 5ms/step - loss: 0.1256 - accuracy: 0.9568 - val_loss: 0.0857 - val_accuracy: 0.9726
Epoch 3/7
99/99 [==============================] - 1s 5ms/step - loss: 0.0864 - accuracy: 0.9720 - val_loss: 0.0753 - val_accuracy: 0.9787
Epoch 4/7
99/99 [==============================] - 0s 5ms/step - loss: 0.0673 - accuracy: 0.9771 - val_loss: 0.0687 - val_accuracy: 0.9802
Epoch 5/7
99/99 [==============================] - 1s 6ms/step - loss: 0.0539 - accuracy: 0.9837 - val_loss: 0.0681 - val_accuracy: 0.9832
Epoch 6/7
99/99 [==============================] - 1s 5ms/step - loss: 0.0466 - accuracy: 0.9878 - val_loss: 0.0704 - val_accuracy: 0.9802
Epoch 7/7
99/99 [==============================] - 1s 5ms/step - loss: 0.0412 - accuracy: 0.9893 - val_loss: 0.0676 - val_accuracy: 0.9817


#### Save preprocessor function to local "preprocessor.zip" file

In [15]:
import aimodelshare as ai
ai.export_preprocessor(preprocessor,"") 

Your preprocessor is now saved to 'preprocessor.zip'


#### Save model to local ".onnx" file

In [16]:
# Save keras model to local ONNX file
from aimodelshare.aimsonnx import model_to_onnx

onnx_model = model_to_onnx(model, framework='keras',
                          transfer_learning=False,
                          deep_learning=True)

with open("model.onnx", "wb") as f:
    f.write(onnx_model.SerializeToString())

## 4. Generate predictions from X_test data and submit model to competition


In [21]:
#Set credentials using modelshare.org username/password

from aimodelshare.aws import set_credentials
    
apiurl = "https://vy08zh602l.execute-api.us-east-1.amazonaws.com/prod/m"
#This is the unique rest api that powers this Internet Ad Prediction Playground

set_credentials(apiurl=apiurl)

AI Modelshare Username:··········
AI Modelshare Password:··········
AI Model Share login credentials set successfully.


In [22]:
#Instantiate Competition
import aimodelshare as ai
mycompetition= ai.Competition(apiurl)

In [23]:
#Submit Model 1: 

#-- Generate predicted y values (Model 1)
#Note: Keras predict returns the predicted column index location for classification models
prediction_column_index=model.predict(preprocessor(X_test)).argmax(axis=1)

# extract correct prediction labels 
prediction_labels = [y_train.columns[i] for i in prediction_column_index]

# Submit Model 1 to Competition Leaderboard
mycompetition.submit_model(model_filepath = "model.onnx",
                                 preprocessor_filepath="preprocessor.zip",
                                 prediction_submission=prediction_labels)

Insert search tags to help users find your model (optional): karthik9
Provide any useful notes about your model (optional): 

Your model has been submitted as model version 1070

To submit code used to create this model or to view current leaderboard navigate to Model Playground: 

 https://www.modelshare.org/detail/model:1464


In [24]:
# Get leaderboard to explore current best model architectures

# Get raw data in pandas data frame
data = mycompetition.get_leaderboard()

# Stylize leaderboard data
mycompetition.stylize_leaderboard(data)

## 5. Repeat submission process to improve place on leaderboard


In [25]:
# Train and submit model 2 using same preprocessor (note that you could save a new preprocessor, but we will use the same one for this example).
import keras
from keras.models import Sequential
from keras.layers import Dense, Dropout, Activation

feature_count=preprocessor(X_train).shape[1] #count features in input data

model_2 = Sequential()
model_2.add(Dense(128, input_dim=feature_count, activation='relu'))
model_2.add(Dropout(.3))
model_2.add(Dense(64, activation='relu'))
model_2.add(Dense(64, activation='relu'))
model_2.add(Dropout(.3))
model_2.add(Dense(64, activation='relu'))

model_2.add(Dense(2, activation='softmax')) 
                                            
# Compile model
model_2.compile(loss='categorical_crossentropy', optimizer='sgd', metrics=['accuracy'])

# Fitting the NN to the Training set
model_2.fit(preprocessor(X_train), y_train, 
               batch_size = 20, 
               epochs = 5, validation_split=0.25) 

Epoch 1/5
99/99 [==============================] - 1s 6ms/step - loss: 0.5224 - accuracy: 0.8607 - val_loss: 0.4026 - val_accuracy: 0.8872
Epoch 2/5
99/99 [==============================] - 0s 5ms/step - loss: 0.4021 - accuracy: 0.8622 - val_loss: 0.3391 - val_accuracy: 0.8872
Epoch 3/5
99/99 [==============================] - 0s 5ms/step - loss: 0.3685 - accuracy: 0.8622 - val_loss: 0.3081 - val_accuracy: 0.8872
Epoch 4/5
99/99 [==============================] - 0s 5ms/step - loss: 0.3425 - accuracy: 0.8622 - val_loss: 0.2800 - val_accuracy: 0.8872
Epoch 5/5
99/99 [==============================] - 0s 5ms/step - loss: 0.3179 - accuracy: 0.8622 - val_loss: 0.2510 - val_accuracy: 0.8872


In [26]:
# Save Model 2 to .onnx file

onnx_model = model_to_onnx(model_2, framework='keras',
                          transfer_learning=False,
                          deep_learning=True)

# Save model to local .onnx file
with open("model_2.onnx", "wb") as f:
    f.write(onnx_model.SerializeToString()) 

In [27]:
# Submit Model 2

#-- Generate predicted y values (Model 2)
#Note: Keras predict returns the predicted column index location for classification models
prediction_column_index=model_2.predict(preprocessor(X_test)).argmax(axis=1)

# extract correct prediction labels 
prediction_labels = [y_train.columns[i] for i in prediction_column_index]

# Submit Model 2 to Competition Leaderboard
mycompetition.submit_model(model_filepath = "model_2.onnx",
                                 prediction_submission=prediction_labels,
                                 preprocessor_filepath="preprocessor.zip")

Insert search tags to help users find your model (optional): karthik9
Provide any useful notes about your model (optional): 

Your model has been submitted as model version 1071

To submit code used to create this model or to view current leaderboard navigate to Model Playground: 

 https://www.modelshare.org/detail/model:1464


In [28]:
# Compare two or more models
data=mycompetition.compare_models([7, 8], verbose=1)
mycompetition.stylize_compare(data)

## Optional: Tune model within range of hyperparameters with Keras Tuner

*Simple example shown below. Consult [documentation](https://keras.io/guides/keras_tuner/getting_started/) to see full functionality.*

In [29]:
! pip install keras_tuner

     |████████████████████████████████| 133 kB 4.6 MB/s 


In [30]:
#Separate validation data 
from sklearn.model_selection import train_test_split
x_train_split, x_val, y_train_split, y_val = train_test_split(
     X_train, y_train, test_size=0.2, random_state=42)

In [31]:
import keras
from keras.models import Sequential
from keras.layers import Dense, Activation, Dropout, BatchNormalization
from keras.regularizers import l1, l2, l1_l2
import keras_tuner as kt


#Define model structure & parameter search space with function
feature_count=preprocessor(X_train).shape[1] #count features in input data

def build_model(hp):
    model = keras.Sequential()
    model.add(Dense(64, input_dim=feature_count, activation='relu', kernel_regularizer=l2(0.01), bias_regularizer=l2(0.01)))
    model.add(Dense(64, activation='relu', kernel_regularizer=l2(0.01), bias_regularizer=l2(0.01)))
    model.add(Dense(units=hp.Int("units", min_value=32, max_value=512, step=32), #range 32-512 inclusive, minimum step between tested values is 32
                    activation='relu', kernel_regularizer=l2(0.01), bias_regularizer=l2(0.01)))
    model.add(Dense(2, activation='softmax')) 
    model.compile(
        optimizer="rmsprop", loss="binary_crossentropy", metrics=["accuracy"],
    )
    return model

#initialize the tuner (which will search through parameters)
tuner = kt.RandomSearch(
    hypermodel=build_model, 
    objective="val_accuracy", # objective to optimize
    max_trials=3, #max number of trials to run during search
    executions_per_trial=3, #higher number reduces variance of results; guages model performance more accurately 
    overwrite=True,
    directory="tuning_model",
    project_name="tuning_units",
)

tuner.search(preprocessor(x_train_split), y_train_split, epochs=1, validation_data=(preprocessor(x_val), y_val))

Trial 3 Complete [00h 00m 11s]
val_accuracy: 0.9276190598805746

Best val_accuracy So Far: 0.9409523804982504
Total elapsed time: 00h 01m 10s


In [32]:
# Build model with best hyperparameters

# Get the top 2 hyperparameters.
best_hps = tuner.get_best_hyperparameters(5)
# Build the model with the best hp.
tuned_model = build_model(best_hps[0])
# Fit with the entire dataset.
tuned_model.fit(x=preprocessor(X_train), y=y_train, epochs=5)

Epoch 1/5
82/82 [==============================] - 1s 6ms/step - loss: 1.2884 - accuracy: 0.9070
Epoch 2/5
82/82 [==============================] - 0s 6ms/step - loss: 0.3203 - accuracy: 0.9661
Epoch 3/5
82/82 [==============================] - 0s 6ms/step - loss: 0.2008 - accuracy: 0.9706
Epoch 4/5
82/82 [==============================] - 0s 5ms/step - loss: 0.1786 - accuracy: 0.9714
Epoch 5/5
82/82 [==============================] - 0s 6ms/step - loss: 0.1676 - accuracy: 0.9699


In [33]:
# Save keras model to local ONNX file
from aimodelshare.aimsonnx import model_to_onnx

onnx_model = model_to_onnx(tuned_model, framework='keras',
                          transfer_learning=False,
                          deep_learning=True)

with open("tuned_model.onnx", "wb") as f:
    f.write(onnx_model.SerializeToString())

In [35]:
#Submit Model 3: 

#-- Generate predicted y values (Model 3)
prediction_column_index=tuned_model.predict(preprocessor(X_test)).argmax(axis=1)

# extract correct prediction labels 
prediction_labels = [y_train.columns[i] for i in prediction_column_index]

# Submit to Competition Leaderboard
mycompetition.submit_model(model_filepath = "tuned_model.onnx",
                                 preprocessor_filepath="preprocessor.zip",
                                 prediction_submission=prediction_labels)

Insert search tags to help users find your model (optional): karthik9
Provide any useful notes about your model (optional): 

Your model has been submitted as model version 1072

To submit code used to create this model or to view current leaderboard navigate to Model Playground: 

 https://www.modelshare.org/detail/model:1464


In [36]:
# Get leaderboard

data = mycompetition.get_leaderboard()
mycompetition.stylize_leaderboard(data)

In [37]:
# Compare two or more models
data=mycompetition.compare_models([7, 8, 9], verbose=1)
mycompetition.stylize_compare(data)